In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn import preprocessing
from sklearn.model_selection import train_test_split

from sklearn import svm
from sklearn import metrics

from sklearn.metrics import classification_report, confusion_matrix

Import 

In [2]:
df_test = pd.read_csv('test_tri_penta.csv')
df_train = pd.read_csv('train_tri_penta.csv') 
df_test_1 = df_test.copy()
df_train_1 = df_train.copy()

df_test_1['Fault Type'] = df_test_1['Fault Type'].replace([1, 2, 3], 0)
df_test_1['Fault Type'] = df_test_1['Fault Type'].replace([4, 5, 6], 1) 
df_train_1['Fault Type'] = df_train_1['Fault Type'].replace([1, 2, 3], 0)
df_train_1['Fault Type'] = df_train_1['Fault Type'].replace([4, 5, 6], 1)

y_test_1 = df_test_1['Fault Type'] 
y_train_1 = df_train_1['Fault Type'] 

x_test = df_test_1.drop(['Fault Type'], axis=1)
x_train = df_train_1.drop(['Fault Type'], axis=1) 

In [3]:
from sklearn import preprocessing
from sklearn.preprocessing import StandardScaler

scaler = StandardScaler()
x_test_n = pd.DataFrame(scaler.fit_transform(x_test), columns=x_test.columns)
x_train_n = pd.DataFrame(scaler.fit_transform(x_train), columns=x_train.columns)

x_test_n.head()

X1        Y1        X2        Y2
0  0.002470  1.866418  0.006314  1.532547
1 -0.115457  1.655284  0.003057  1.659582
2 -0.229044  1.424407  0.003096  1.756957
3 -1.906439 -1.551226 -1.511158  1.123731
4  0.002470  1.865438  0.017065  1.698771

# The first layer

In [4]:
import optuna
from sklearn import svm
from sklearn import metrics

# Define the objective function for Optuna
def objective(trial):
    # Define the search space for hyperparameters
    c = trial.suggest_float('C', 0.001, 20)
    gamma = trial.suggest_float('gamma', 0.0001, 20)  # Adjusted to a common range for gamma
    kernel = trial.suggest_categorical('kernel', ['linear', 'poly', 'rbf', 'sigmoid'])
    degree = trial.suggest_int('degree', 1, 5)
    shrinking = trial.suggest_categorical('shrinking', [True, False])
    tol = trial.suggest_float('tol', 1e-5, 1e-1)
    decision_function_shape = trial.suggest_categorical('decision_function_shape', ['ovo'])
    break_ties = trial.suggest_categorical('break_ties', [False])
    probability = trial.suggest_categorical('probability', [False,True])
    # Create an SVM classifier with the hyperparameters
    clf = svm.SVC(C=c, gamma=gamma, kernel=kernel, degree=degree, shrinking=shrinking,tol=tol,
                   decision_function_shape=decision_function_shape, break_ties=break_ties, probability=probability)

    # Fit the classifier on the training data
    clf.fit(x_train_n, y_train_1)  # Assuming x_train_n and y_train_1 are defined

    # Predict the labels for the test data
    y_pred = clf.predict(x_test_n)  # Assuming x_test_n is defined

    # Calculate the accuracy of the classifier
    accuracy = metrics.accuracy_score(y_test_1, y_pred)  # Assuming y_test_1 is defined

    # Return the accuracy
    return accuracy

# Create a study object and optimize the hyperparameters
study = optuna.create_study(direction='maximize')
study.optimize(objective, n_trials=1000)

# Get the best hyperparameters
best_params = study.best_params
best_accuracy = study.best_value

print('Best accuracy:', best_accuracy)
print('Best parameters:', best_params)


[I 2024-05-30 16:17:26,770] A new study created in memory with name: no-name-9df90f44-173b-4505-99cb-8c261ee5834d
[I 2024-05-30 16:17:26,779] Trial 0 finished with value: 0.65625 and parameters: {'C': 8.734888412681642, 'gamma': 5.00738540347114, 'kernel': 'sigmoid', 'degree': 3, 'shrinking': False, 'tol': 0.07360317229619555, 'decision_function_shape': 'ovo', 'break_ties': False, 'probability': False}. Best is trial 0 with value: 0.65625.
[I 2024-05-30 16:17:26,792] Trial 1 finished with value: 0.98125 and parameters: {'C': 19.39840923399769, 'gamma': 1.5426474949497502, 'kernel': 'rbf', 'degree': 2, 'shrinking': False, 'tol': 0.06248781744489845, 'decision_function_shape': 'ovo', 'break_ties': False, 'probability': True}. Best is trial 1 with value: 0.98125.
[I 2024-05-30 16:17:26,869] Trial 2 finished with value: 0.8625 and parameters: {'C': 1.1276119653763004, 'gamma': 9.87213992576335, 'kernel': 'poly', 'degree': 2, 'shrinking': True, 'tol': 0.02911220929838474, 'decision_function

: 

: 

# The 2nd layer of tree's (D1 D2 D3)

In [4]:
df_test_D = df_test.copy()
df_train_D = df_train.copy() 

# Filter the training data
df_train_D_filtered = df_train_D[df_train_D['Fault Type'].isin([1, 2, 3])]

# Filter the test data
df_test_D_filtered = df_test_D[df_test_D['Fault Type'].isin([1, 2, 3])]

# Optionally, reset the index if needed
df_train_D_filtered.reset_index(drop=True, inplace=True)
df_test_D_filtered.reset_index(drop=True, inplace=True)

y_test_D = df_test_D_filtered['Fault Type']
y_train_D = df_train_D_filtered['Fault Type']

df_train_D_f = df_train_D_filtered.drop('Fault Type', axis=1)
df_test_D_f = df_test_D_filtered.drop('Fault Type', axis=1)
# preprocces it with normalizing 

df_train_Dn = pd.DataFrame(preprocessing.robust_scale(df_train_D_filtered.drop(['Fault Type'], axis=1)), columns=df_train_D_filtered.drop(['Fault Type'], axis=1).columns)
df_test_Dn = pd.DataFrame(preprocessing.robust_scale(df_test_D_filtered.drop(['Fault Type'], axis=1)), columns=df_test_D_filtered.drop(['Fault Type'], axis=1).columns)

In [37]:
import optuna
from sklearn import svm
from sklearn import metrics

# Define the objective function for Optuna
def objective(trial):
    # Define the search space for hyperparameters
    c = trial.suggest_float('C', 0.1, 20)
    gamma = trial.suggest_float('gamma', 0.1, 20)  # Adjusted to a common range for gamma
    kernel = trial.suggest_categorical('kernel', ['poly'])
    degree = trial.suggest_int('degree', 1, 5) 
    shrinking = trial.suggest_categorical('shrinking', [True, False])
    tol = trial.suggest_float('tol', 1e-5, 1e-1)
    decision_function_shape = trial.suggest_categorical('decision_function_shape', ['ovo'])
    break_ties = trial.suggest_categorical('break_ties', [False])
    probability = trial.suggest_categorical('probability', [False,True])
    # Create an SVM classifier with the hyperparameters
    clf = svm.SVC(C=c, gamma=gamma, kernel=kernel, degree=degree, shrinking=shrinking,tol=tol,
        decision_function_shape=decision_function_shape, break_ties=break_ties, probability=probability)

    # Fit the classifier on the training data
    clf.fit(df_train_Dn, y_train_D)  # Assuming x_train_n and y_train_1 are defined

    # Predict the labels for the test data
    y_pred = clf.predict(df_test_Dn)  # Assuming x_test_n is defined

    # Calculate the accuracy of the classifier
    accuracy = metrics.accuracy_score(y_test_D, y_pred)  # Assuming y_test_1 is defined

    # Return the accuracy
    return accuracy

# Create a study object and optimize the hyperparameters
study = optuna.create_study(direction='maximize')
study.optimize(objective, n_trials=1000)

# Get the best hyperparameters
best_params = study.best_params
best_accuracy = study.best_value

print('Best accuracy:', best_accuracy)
print('Best parameters:', best_params)


[I 2024-05-27 18:02:06,942] A new study created in memory with name: no-name-7a57ecb8-54c9-4570-9578-9df249d9e9e0


[I 2024-05-27 18:02:07,909] Trial 0 finished with value: 0.8214285714285714 and parameters: {'C': 6.915088073619687, 'gamma': 17.733328494772483, 'kernel': 'poly', 'degree': 4, 'shrinking': False, 'tol': 0.046826167123739895, 'decision_function_shape': 'ovr', 'break_ties': True, 'probability': False}. Best is trial 0 with value: 0.8214285714285714.
[I 2024-05-27 18:02:07,913] Trial 1 finished with value: 0.5 and parameters: {'C': 9.919783580380093, 'gamma': 14.636423351134669, 'kernel': 'sigmoid', 'degree': 2, 'shrinking': True, 'tol': 0.003915932752930868, 'decision_function_shape': 'ovr', 'break_ties': True, 'probability': False}. Best is trial 0 with value: 0.8214285714285714.
[I 2024-05-27 18:02:07,920] Trial 2 finished with value: 0.4880952380952381 and parameters: {'C': 16.723866151731514, 'gamma': 1.9315263543754984, 'kernel': 'sigmoid', 'degree': 5, 'shrinking': True, 'tol': 0.06985199260654563, 'decision_function_shape': 'ovr', 'break_ties': True, 'probability': True}. Best is

Best accuracy: 0.9404761904761905
Best parameters: {'C': 11.209436615998207, 'gamma': 5.175458132628451, 'kernel': 'rbf', 'degree': 5, 'shrinking': True, 'tol': 0.09620429932986038, 'decision_function_shape': 'ovr', 'break_ties': True, 'probability': False}


# The 2nd layer of tree's (T1 T2 T3)

In [14]:
df_test_T = df_test.copy()
df_train_T = df_train.copy() 

# Filter the training data
df_train_T_filtered = df_train_T[df_train_T['Fault Type'].isin([4, 5, 6])]

# Filter the test data
df_test_T_filtered = df_test_T[df_test_T['Fault Type'].isin([4, 5, 6])]

# Optionally, reset the index if needed
df_train_T_filtered.reset_index(drop=True, inplace=True)
df_test_T_filtered.reset_index(drop=True, inplace=True)

y_test_T = df_test_T_filtered['Fault Type']
y_train_T = df_train_T_filtered['Fault Type']

# preprocces it with normalizing 

df_train_Tn = pd.DataFrame(preprocessing.robust_scale(df_train_T_filtered.drop(['Fault Type'], axis=1)), columns=df_train_T_filtered.drop(['Fault Type'], axis=1).columns)
df_test_Tn = pd.DataFrame(preprocessing.robust_scale(df_test_T_filtered.drop(['Fault Type'], axis=1)), columns=df_test_T_filtered.drop(['Fault Type'], axis=1).columns)


In [10]:
import optuna
from sklearn import svm
from sklearn import metrics

# Define the objective function for Optuna
def objective(trial):
    # Define the search space for hyperparameters
    c = trial.suggest_float('C', 0.0001, 20)
    gamma = trial.suggest_float('gamma', 0.0001, 20)  # Adjusted to a common range for gamma
    kernel = trial.suggest_categorical('kernel', ['linear', 'poly', 'rbf', 'sigmoid'])
    degree = trial.suggest_int('degree', 1, 5) 
    shrinking = trial.suggest_categorical('shrinking', [True, False])
    tol = trial.suggest_float('tol', 1e-5, 1e-1)
    decision_function_shape = trial.suggest_categorical('decision_function_shape', ['ovr'])
    break_ties = trial.suggest_categorical('break_ties', [True])
    probability = trial.suggest_categorical('probability', [False,True])
    # Create an SVM classifier with the hyperparameters
    clf = svm.SVC(C=c, gamma=gamma, kernel=kernel, degree=degree, shrinking=shrinking,tol=tol,
        decision_function_shape=decision_function_shape, break_ties=break_ties, probability=probability)

    # Fit the classifier on the training data
    clf.fit(df_train_Tn, y_train_T)  # Assuming x_train_n and y_train_1 are defined

    # Predict the labels for the test data
    y_pred = clf.predict(df_test_Tn)  # Assuming x_test_n is defined

    # Calculate the accuracy of the classifier
    accuracy = metrics.accuracy_score(y_test_T, y_pred)  # Assuming y_test_1 is defined

    # Return the accuracy
    return accuracy

# Create a study object and optimize the hyperparameters
study = optuna.create_study(direction='maximize')
study.optimize(objective, n_trials=1000)

# Get the best hyperparameters
best_params = study.best_params
best_accuracy = study.best_value

print('Best accuracy:', best_accuracy)
print('Best parameters:', best_params)


[I 2024-05-28 22:54:04,608] A new study created in memory with name: no-name-4014536a-39e4-469d-8e0c-cfb0fce2235d
[I 2024-05-28 22:54:04,651] Trial 0 finished with value: 0.5 and parameters: {'C': 18.11171683693653, 'gamma': 15.903958531802504, 'kernel': 'sigmoid', 'degree': 3, 'shrinking': False, 'tol': 0.08564929212452194, 'decision_function_shape': 'ovr', 'break_ties': True, 'probability': True}. Best is trial 0 with value: 0.5.
[I 2024-05-28 22:54:04,714] Trial 1 finished with value: 0.8947368421052632 and parameters: {'C': 6.344290217549891, 'gamma': 19.565101163830654, 'kernel': 'poly', 'degree': 3, 'shrinking': True, 'tol': 0.0787926649921958, 'decision_function_shape': 'ovr', 'break_ties': True, 'probability': False}. Best is trial 1 with value: 0.8947368421052632.
[I 2024-05-28 22:54:04,721] Trial 2 finished with value: 0.7368421052631579 and parameters: {'C': 15.611106440725798, 'gamma': 2.1435550553509146, 'kernel': 'sigmoid', 'degree': 3, 'shrinking': False, 'tol': 0.098027

KeyboardInterrupt: 

# 3rd Layer (D1,D23  D2,D13   D3,D12) 

## D1 D23

In [15]:
df_train_D_f23 = df_train_D_filtered.copy()
df_test_D_f23 = df_test_D_filtered.copy()

df_train_D_f23['Fault Type'] = df_train_D_f23['Fault Type'].replace([2, 3], 0)
df_test_D_f23['Fault Type'] = df_test_D_f23['Fault Type'].replace([2,3],0)  
df_train_D_f23['Fault Type'] = df_train_D_f23['Fault Type'].replace([1],1)  
df_test_D_f23['Fault Type'] = df_test_D_f23['Fault Type'].replace([1],1)  


df_train_D_f23.reset_index(drop=True, inplace=True)
df_test_D_f23.reset_index(drop=True, inplace=True)


y_test_D1_23 = df_test_D_f23['Fault Type']
y_train_D1_23 = df_train_D_f23['Fault Type']  

df_train_D1_23 = df_train_D_f23.drop('Fault Type',axis=1)
df_test_D1_23 = df_test_D_f23.drop('Fault Type',axis=1) 

df_train_D1_23n = pd.DataFrame(preprocessing.robust_scale(df_train_D1_23),columns=df_train_D1_23.columns)
df_test_D1_23n = pd.DataFrame(preprocessing.robust_scale(df_test_D1_23),columns=df_test_D1_23.columns) 

df_train_D_f23.head()

X1         Y1        X2         Y2  Fault Type
0  1.080000e-15  56.140351 -0.469846  20.749464           1
1 -2.013831e+01  31.781431 -1.018934  24.696538           1
2  2.410000e-18  66.633344 -0.099776  -1.131513           1
3 -3.718366e+01   2.259284 -5.342724  22.232791           1
4 -1.480385e+01  25.641026 -2.668719  19.005826           1

In [16]:
import optuna
from sklearn import svm
from sklearn import metrics

# Define the objective function for Optuna
def objective(trial):
    # Define the search space for hyperparameters
    c = trial.suggest_float('C', 0.01, 20)
    gamma = trial.suggest_float('gamma', 0.01, 20)  # Adjusted to a common range for gamma
    kernel = trial.suggest_categorical('kernel', ['linear', 'poly', 'rbf', 'sigmoid'])
    degree = trial.suggest_int('degree', 1, 4) 
    shrinking = trial.suggest_categorical('shrinking', [True, False])
    tol = trial.suggest_float('tol', 1e-3, 1e-1)
    decision_function_shape = trial.suggest_categorical('decision_function_shape', ['ovr'])
    break_ties = trial.suggest_categorical('break_ties', [True])
    probability = trial.suggest_categorical('probability', [False,True])
    random_state = trial.suggest_int('random_state', 1, 100)
    # Create an SVM classifier with the hyperparameters
    clf = svm.SVC(C=c, gamma=gamma, kernel=kernel, degree=degree, shrinking=shrinking,tol=tol,
        decision_function_shape=decision_function_shape, break_ties=break_ties, probability=probability ,random_state=random_state)

    # Fit the classifier on the training data
    clf.fit(df_train_D1_23n, y_train_D1_23)  # Assuming x_train_n and y_train_1 are defined

    # Predict the labels for the test data
    y_pred = clf.predict(df_test_D1_23n)  # Assuming x_test_n is defined

    # Calculate the accuracy of the classifier
    accuracy = metrics.accuracy_score(y_test_D1_23, y_pred)  # Assuming y_test_1 is defined

    # Return the accuracy
    return accuracy

# Create a study object and optimize the hyperparameters
study = optuna.create_study(direction='maximize')
study.optimize(objective, n_trials=1000)

# Get the best hyperparameters
best_params = study.best_params
best_accuracy = study.best_value

print('Best accuracy:', best_accuracy)
print('Best parameters:', best_params)


[I 2024-05-30 17:42:25,506] A new study created in memory with name: no-name-4e35f510-5af5-4fb4-901c-ff760c40766f


[I 2024-05-30 17:42:25,532] Trial 0 finished with value: 0.6071428571428571 and parameters: {'C': 15.411285297366287, 'gamma': 12.990476300588575, 'kernel': 'sigmoid', 'degree': 2, 'shrinking': True, 'tol': 0.07869206184170921, 'decision_function_shape': 'ovr', 'break_ties': True, 'probability': False, 'random_state': 53}. Best is trial 0 with value: 0.6071428571428571.
[I 2024-05-30 17:42:25,539] Trial 1 finished with value: 0.7976190476190477 and parameters: {'C': 17.47813305667022, 'gamma': 18.04838616253772, 'kernel': 'rbf', 'degree': 4, 'shrinking': False, 'tol': 0.027001423379719888, 'decision_function_shape': 'ovr', 'break_ties': True, 'probability': False, 'random_state': 80}. Best is trial 1 with value: 0.7976190476190477.
[I 2024-05-30 17:42:25,547] Trial 2 finished with value: 0.6309523809523809 and parameters: {'C': 17.450420199519673, 'gamma': 1.9020525425194081, 'kernel': 'sigmoid', 'degree': 4, 'shrinking': False, 'tol': 0.05378074839036972, 'decision_function_shape': 'o

KeyboardInterrupt: 

## D23

In [5]:
df_test_D23 = df_test.copy()
df_train_D23 = df_train.copy() 

# Filter the training data
df_train_D23_f = df_train_D23[df_train_D23['Fault Type'].isin([2, 3])]
# Filter the test data
df_test_D23_f = df_test_D23[df_test_D23['Fault Type'].isin([2, 3])]

# Optionally, reset the index if needed
df_train_D23_f.reset_index(drop=True, inplace=True)
df_test_D23_f.reset_index(drop=True, inplace=True)

y_test_D23 = df_test_D23_f['Fault Type']
y_train_D23 = df_train_D23_f['Fault Type'] 
# preprocces it with normalizing  

df_train_D23n = pd.DataFrame(preprocessing.robust_scale(df_train_D23_f.drop(['Fault Type'], axis=1)), columns=df_train_D23_f.drop(['Fault Type'], axis=1).columns)
df_test_D23n = pd.DataFrame(preprocessing.robust_scale(df_test_D23_f.drop(['Fault Type'], axis=1)), columns=df_test_D23_f.drop(['Fault Type'], axis=1).columns)


In [6]:
import optuna
from sklearn import svm
from sklearn import metrics

# Define the objective function for Optuna
def objective(trial):
    # Define the search space for hyperparameters
    c = trial.suggest_float('C', 0.1, 1)
    gamma = trial.suggest_float('gamma', 1, 20)  # Adjusted to a common range for gamma
    shrinking = trial.suggest_categorical('shrinking', [True, False])
    probability = trial.suggest_categorical('probability', [False,True])
    random_state = trial.suggest_int('random_state', 1, 100)
    degree = trial.suggest_int('degree', 1, 4) 
    kernel = trial.suggest_categorical('kernel', ['poly'])
    # Create an SVM classifier with the hyperparameters
    clf = svm.SVC(C=c, gamma=gamma, kernel=kernel, degree=degree, shrinking=shrinking,
                   probability=probability,random_state=random_state)

    # Fit the classifier on the training data
    clf.fit(df_train_D23n, y_train_D23)  # Assuming x_train_n and y_train_1 are defined

    # Predict the labels for the test data
    y_pred = clf.predict(df_test_D23n)  # Assuming x_test_n is defined

    # Calculate the accuracy of the classifier
    accuracy = metrics.accuracy_score(y_test_D23, y_pred)  # Assuming y_test_1 is defined

    # Return the accuracy
    return accuracy

# Create a study object and optimize the hyperparameters
study = optuna.create_study(direction='maximize')
study.optimize(objective, n_trials=10)

# Get the best hyperparameters
best_params = study.best_params
best_accuracy = study.best_value

print('Best accuracy:', best_accuracy)
print('Best parameters:', best_params)

[I 2024-06-03 23:04:08,950] A new study created in memory with name: no-name-74b0b024-f7a2-4c8b-9a61-2dfe1ac2b71e
[I 2024-06-03 23:04:08,964] Trial 0 finished with value: 0.75 and parameters: {'C': 0.3227427950515484, 'gamma': 2.5444236307993267, 'shrinking': False, 'probability': False, 'random_state': 88, 'degree': 3, 'kernel': 'poly'}. Best is trial 0 with value: 0.75.
[I 2024-06-03 23:04:09,324] Trial 1 finished with value: 0.6764705882352942 and parameters: {'C': 0.32414048765660786, 'gamma': 15.831814218350665, 'shrinking': False, 'probability': True, 'random_state': 1, 'degree': 2, 'kernel': 'poly'}. Best is trial 0 with value: 0.75.


## D2 D13 

In [77]:
df_train_D_f13 = df_train_D_filtered.copy()
df_test_D_f13 = df_test_D_filtered.copy()

df_train_D_f13['Fault Type'] = df_train_D_f13['Fault Type'].replace([1, 3], 0)
df_test_D_f13['Fault Type'] = df_test_D_f13['Fault Type'].replace([1,3],0)  
df_train_D_f13['Fault Type'] = df_train_D_f13['Fault Type'].replace([2],1)  
df_test_D_f13['Fault Type'] = df_test_D_f13['Fault Type'].replace([2],1)  


df_train_D_f13.reset_index(drop=True, inplace=True)
df_test_D_f13.reset_index(drop=True, inplace=True)


y_test_D2_13 = df_test_D_f13['Fault Type']
y_train_D2_13 = df_train_D_f13['Fault Type']  

df_train_D2_13 = df_train_D_f13.drop('Fault Type',axis=1)
df_test_D2_13 = df_test_D_f13.drop('Fault Type',axis=1) 

df_train_D2_13n = pd.DataFrame(preprocessing.normalize(df_train_D2_13),columns=df_train_D2_13.columns)
df_test_D2_13n = pd.DataFrame(preprocessing.normalize(df_test_D2_13),columns=df_test_D2_13.columns) 

df_train_D_f13.head()

H2   CH4   C2H2  C2H4    C2H6  Fault Type
0  117.0  17.0  1.000   3.0   1.000           0
1  407.0  28.0  0.001  21.0  15.000           0
2  183.0   6.0  0.001   5.0   0.001           0
3  166.0  21.0  0.001   6.0  38.000           0
4  105.0  23.0  3.000   4.0  13.000           0

In [85]:
import optuna
from sklearn import svm
from sklearn import metrics

# Define the objective function for Optuna
def objective(trial):
    # Define the search space for hyperparameters
    c = trial.suggest_float('C', 0.01, 20)
    gamma = trial.suggest_float('gamma', 0.01, 20)  # Adjusted to a common range for gamma
    kernel = trial.suggest_categorical('kernel', ['linear', 'poly', 'rbf', 'sigmoid'])
    degree = trial.suggest_int('degree', 1, 4) 
    shrinking = trial.suggest_categorical('shrinking', [True, False])
    tol = trial.suggest_float('tol', 1e-3, 1e-1)
    decision_function_shape = trial.suggest_categorical('decision_function_shape', ['ovr'])
    break_ties = trial.suggest_categorical('break_ties', [True])
    probability = trial.suggest_categorical('probability', [False,True])
    random_state = trial.suggest_int('random_state', 1, 100)
     
    # Create an SVM classifier with the hyperparameters
    clf = svm.SVC(C=c, gamma=gamma, kernel=kernel, degree=degree, shrinking=shrinking,tol=tol,
        decision_function_shape=decision_function_shape, break_ties=break_ties, probability=probability, random_state=random_state)

    # Fit the classifier on the training data
    clf.fit(df_train_D2_13n, y_train_D2_13)  # Assuming x_train_n and y_train_1 are defined

    # Predict the labels for the test data
    y_pred = clf.predict(df_test_D2_13n)  # Assuming x_test_n is defined

    # Calculate the accuracy of the classifier
    accuracy = metrics.accuracy_score(y_test_D2_13, y_pred)  # Assuming y_test_1 is defined

    # Return the accuracy
    return accuracy

# Create a study object and optimize the hyperparameters
study = optuna.create_study(direction='maximize')
study.optimize(objective, n_trials=2000)

# Get the best hyperparameters
best_params = study.best_params
best_accuracy = study.best_value

print('Best accuracy:', best_accuracy)
print('Best parameters:', best_params)


[I 2024-05-28 12:31:54,753] A new study created in memory with name: no-name-2f64d8bb-cf96-4f84-896a-aeab7dd40f59
[I 2024-05-28 12:31:54,773] Trial 0 finished with value: 0.5952380952380952 and parameters: {'C': 8.760636056511023, 'gamma': 14.754225665107626, 'kernel': 'sigmoid', 'degree': 1, 'shrinking': False, 'tol': 0.06222975865684146, 'decision_function_shape': 'ovr', 'break_ties': True, 'probability': False, 'random_state': 81}. Best is trial 0 with value: 0.5952380952380952.
[I 2024-05-28 12:31:54,800] Trial 1 finished with value: 0.8690476190476191 and parameters: {'C': 1.7038104321963157, 'gamma': 8.51175849977289, 'kernel': 'poly', 'degree': 4, 'shrinking': True, 'tol': 0.07694034739710919, 'decision_function_shape': 'ovr', 'break_ties': True, 'probability': False, 'random_state': 1}. Best is trial 1 with value: 0.8690476190476191.


[I 2024-05-28 12:31:55,021] Trial 2 finished with value: 0.8809523809523809 and parameters: {'C': 10.178366325130494, 'gamma': 7.566626032056765, 'kernel': 'poly', 'degree': 3, 'shrinking': False, 'tol': 0.02072591016051613, 'decision_function_shape': 'ovr', 'break_ties': True, 'probability': True, 'random_state': 9}. Best is trial 2 with value: 0.8809523809523809.
[I 2024-05-28 12:31:55,025] Trial 3 finished with value: 0.5357142857142857 and parameters: {'C': 5.2662997670315495, 'gamma': 6.761877761753449, 'kernel': 'sigmoid', 'degree': 4, 'shrinking': True, 'tol': 0.08230612154816969, 'decision_function_shape': 'ovr', 'break_ties': True, 'probability': False, 'random_state': 30}. Best is trial 2 with value: 0.8809523809523809.
[I 2024-05-28 12:31:55,403] Trial 4 finished with value: 0.8333333333333334 and parameters: {'C': 16.017419542071618, 'gamma': 5.654146750394917, 'kernel': 'poly', 'degree': 4, 'shrinking': False, 'tol': 0.01363753252343285, 'decision_function_shape': 'ovr', '

Best accuracy: 0.9404761904761905
Best parameters: {'C': 19.17900281308865, 'gamma': 14.968030756676903, 'kernel': 'rbf', 'degree': 3, 'shrinking': True, 'tol': 0.010350663153745701, 'decision_function_shape': 'ovr', 'break_ties': True, 'probability': True, 'random_state': 39}


## D13

In [82]:
df_test_D13 = df_test.copy()
df_train_D13 = df_train.copy() 

# Filter the training data1df_train_D13_f = df_train_D13[df_train_D13['Fault Type'].isin([1, 3])]
# Filter the test data
df_test_D13_f = df_test_D13[df_test_D13['Fault Type'].isin([1, 3])]
df_train_D13_f = df_train_D13[df_train_D13['Fault Type'].isin([1, 3])]

# Optionally, reset the index if needed
df_train_D13_f.reset_index(drop=True, inplace=True)
df_test_D13_f.reset_index(drop=True, inplace=True)

y_test_D13 = df_test_D13_f['Fault Type']
y_train_D13 = df_train_D13_f['Fault Type'] 
# preprocces it with normalizing  

df_train_D13n = pd.DataFrame(preprocessing.normalize(df_train_D13_f.drop(['Fault Type'], axis=1)), columns=df_train_D13_f.drop(['Fault Type'], axis=1).columns)
df_test_D13n = pd.DataFrame(preprocessing.normalize(df_test_D13_f.drop(['Fault Type'], axis=1)), columns=df_test_D13_f.drop(['Fault Type'], axis=1).columns)


In [83]:
import optuna
from sklearn import svm
from sklearn import metrics

# Define the objective function for Optuna
def objective(trial):
    # Define the search space for hyperparameters
    c = trial.suggest_float('C', 0.01, 10)
    gamma = trial.suggest_float('gamma', 0.01, 10)  # Adjusted to a common range for gamma
    kernel = trial.suggest_categorical('kernel', ['linear', 'poly', 'rbf', 'sigmoid'])
    degree = trial.suggest_int('degree', 1, 4) 
    shrinking = trial.suggest_categorical('shrinking', [True, False])
    tol = trial.suggest_float('tol', 1e-3, 1e-1)
    decision_function_shape = trial.suggest_categorical('decision_function_shape', ['ovo'])
    break_ties = trial.suggest_categorical('break_ties', [False])
    probability = trial.suggest_categorical('probability', [False,True])
    random_state = trial.suggest_int('random_state', 1, 100)
    # Create an SVM classifier with the hyperparameters
    clf = svm.SVC(C=c, gamma=gamma, kernel=kernel, degree=degree, shrinking=shrinking,tol=tol,
        decision_function_shape=decision_function_shape, break_ties=break_ties, probability=probability, random_state=random_state)

    # Fit the classifier on the training data
    clf.fit(df_train_D13n, y_train_D13)  # Assuming x_train_n and y_train_1 are defined

    # Predict the labels for the test data
    y_pred = clf.predict(df_test_D13n)  # Assuming x_test_n is defined

    # Calculate the accuracy of the classifier
    accuracy = metrics.accuracy_score(y_test_D13, y_pred)  # Assuming y_test_1 is defined

    # Return the accuracy
    return accuracy

# Create a study object and optimize the hyperparameters
study = optuna.create_study(direction='maximize')
study.optimize(objective, n_trials=2000)

# Get the best hyperparameters
best_params = study.best_params
best_accuracy = study.best_value

print('Best accuracy:', best_accuracy)
print('Best parameters:', best_params)

[I 2024-05-28 12:25:04,634] A new study created in memory with name: no-name-60298ebb-61c7-42cc-ba12-40c2914c78f2
[I 2024-05-28 12:25:04,665] Trial 0 finished with value: 1.0 and parameters: {'C': 7.567048177885438, 'gamma': 2.80939782858393, 'kernel': 'linear', 'degree': 1, 'shrinking': True, 'tol': 0.02236936403593737, 'decision_function_shape': 'ovo', 'break_ties': False, 'probability': False, 'random_state': 81}. Best is trial 0 with value: 1.0.
[I 2024-05-28 12:25:04,670] Trial 1 finished with value: 1.0 and parameters: {'C': 3.3021751535411497, 'gamma': 3.4023518506179546, 'kernel': 'poly', 'degree': 3, 'shrinking': False, 'tol': 0.0877343081440287, 'decision_function_shape': 'ovo', 'break_ties': False, 'probability': True, 'random_state': 3}. Best is trial 0 with value: 1.0.
[I 2024-05-28 12:25:04,674] Trial 2 finished with value: 0.9827586206896551 and parameters: {'C': 8.298130212872731, 'gamma': 3.415173629469327, 'kernel': 'poly', 'degree': 4, 'shrinking': False, 'tol': 0.09

Best accuracy: 1.0
Best parameters: {'C': 7.567048177885438, 'gamma': 2.80939782858393, 'kernel': 'linear', 'degree': 1, 'shrinking': True, 'tol': 0.02236936403593737, 'decision_function_shape': 'ovo', 'break_ties': False, 'probability': False, 'random_state': 81}


## D3 D12

In [7]:
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import MinMaxScaler, RobustScaler, StandardScaler, PowerTransformer
from sklearn import preprocessing

df_train_D_f12 = df_train_D_filtered.copy()
df_test_D_f12 = df_test_D_filtered.copy()

df_train_D_f12['Fault Type'] = df_train_D_f12['Fault Type'].replace([1, 2], 0)
df_test_D_f12['Fault Type'] = df_test_D_f12['Fault Type'].replace([1,2],0)  
df_train_D_f12['Fault Type'] = df_train_D_f12['Fault Type'].replace([3],1)  
df_test_D_f12['Fault Type'] = df_test_D_f12['Fault Type'].replace([3],1)  


df_train_D_f12.reset_index(drop=True, inplace=True)
df_test_D_f12.reset_index(drop=True, inplace=True)


y_test_D3_12 = df_test_D_f12['Fault Type']
y_train_D3_12 = df_train_D_f12['Fault Type']  

df_train_D3_12 = df_train_D_f12.drop('Fault Type',axis=1)
df_test_D3_12 = df_test_D_f12.drop('Fault Type',axis=1) 

df_train_D3_12n = pd.DataFrame(preprocessing.normalize(df_train_D3_12),columns=df_train_D3_12.columns)
df_test_D3_12n = pd.DataFrame(preprocessing.normalize(df_test_D3_12),columns=df_test_D3_12.columns)




# Preprocess the training data using StandardScaler
scaler = StandardScaler()
df_train_D3_12_StandardScaler = scaler.fit_transform(df_train_D3_12)

# Preprocess the test data using StandardScaler
df_test_D3_12_StandardScaler = scaler.transform(df_test_D3_12)

# Preprocess the training data using MinMaxScaler
scaler = MinMaxScaler()
df_train_D3_12_MinMaxScaler = scaler.fit_transform(df_train_D3_12)

# Preprocess the test data using MinMaxScaler
df_test_D3_12_MinMaxScaler = scaler.transform(df_test_D3_12)

# Preprocess the training data using RobustScaler
scaler = RobustScaler()
df_train_D3_12_RobustScaler = scaler.fit_transform(df_train_D3_12)

# Preprocess the test data using RobustScaler
df_test_D3_12_RobustScaler = scaler.transform(df_test_D3_12)

# Preprocess the training data using PowerTransformer
scaler = PowerTransformer()
df_train_D3_12_PowerTransformer = scaler.fit_transform(df_train_D3_12)

# Preprocess the test data using PowerTransformer
df_test_D3_12_PowerTransformer = scaler.transform(df_test_D3_12)

In [8]:
import optuna
from sklearn import svm
from sklearn import metrics

# Define the objective function for Optuna
def objective(trial):
    # Define the search space for hyperparameters
    c = trial.suggest_float('C', 0.1, 20)
    gamma = trial.suggest_float('gamma', 1, 20)  # Adjusted to a common range for gamma 
    shrinking = trial.suggest_categorical('shrinking', [True, False])
    tol = trial.suggest_float('tol', 1e-5, 1e-3)
    decision_function_shape = trial.suggest_categorical('decision_function_shape', ['ovo'])
    break_ties = trial.suggest_categorical('break_ties', [False])
    probability = trial.suggest_categorical('probability', [False,True])
    random_state = trial.suggest_int('random_state', 1, 100)
    kernel = trial.suggest_categorical('kernel', ['linear', 'poly', 'rbf', 'sigmoid'])
    degree = trial.suggest_int('degree', 1, 4)
    # Create an SVM classifier with the hyperparameters
    
    clf = svm.SVC(C=c, gamma=gamma, kernel=kernel, degree=degree, shrinking=shrinking,tol=tol,
        decision_function_shape=decision_function_shape, break_ties=break_ties, probability=probability,random_state=random_state)

    # Fit the classifier on the training data
    clf.fit(df_train_D3_12n, y_train_D3_12)  # Assuming x_train_n and y_train_1 are defined

    # Predict the labels for the test data
    y_pred = clf.predict(df_test_D3_12n)  # Assuming x_test_n is defined

    # Calculate the accuracy of the classifier 
    accuracy = metrics.accuracy_score(y_test_D3_12, y_pred)  # Assuming y_test_1 is defined

    # Return the accuracy
    return accuracy

# Create a study object and optimize the hyperparameters
study = optuna.create_study(direction='maximize')
study.optimize(objective, n_trials=1000)

# Get the best hyperparameters
best_params = study.best_params
best_accuracy = study.best_value

print('Best accuracy:', best_accuracy)
print('Best parameters:', best_params)

[I 2024-05-28 19:06:09,911] A new study created in memory with name: no-name-928a60b1-75be-409d-8244-ea4d893866d4
[I 2024-05-28 19:06:09,927] Trial 0 finished with value: 0.32142857142857145 and parameters: {'C': 10.487254639911985, 'gamma': 11.193394176379007, 'shrinking': False, 'tol': 0.00025505945062165666, 'decision_function_shape': 'ovo', 'break_ties': False, 'probability': True, 'random_state': 6, 'kernel': 'sigmoid', 'degree': 3}. Best is trial 0 with value: 0.32142857142857145.
[I 2024-05-28 19:06:09,937] Trial 1 finished with value: 0.30952380952380953 and parameters: {'C': 8.273250017813966, 'gamma': 15.172496613178454, 'shrinking': True, 'tol': 0.00011136619969684218, 'decision_function_shape': 'ovo', 'break_ties': False, 'probability': True, 'random_state': 18, 'kernel': 'sigmoid', 'degree': 4}. Best is trial 0 with value: 0.32142857142857145.
[I 2024-05-28 19:06:09,941] Trial 2 finished with value: 0.8571428571428571 and parameters: {'C': 8.422571975608296, 'gamma': 11.20

KeyboardInterrupt: 

## D12

In [90]:
df_test_D12 = df_test.copy()
df_train_D12 = df_train.copy() 

# Filter the training data1df_train_D13_f = df_train_D13[df_train_D13['Fault Type'].isin([1, 3])]
# Filter the test data
df_test_D12_f = df_test_D12[df_test_D12['Fault Type'].isin([1, 3])]
df_train_D12_f = df_train_D12[df_train_D12['Fault Type'].isin([1, 3])]

# Optionally, reset the index if needed
df_train_D12_f.reset_index(drop=True, inplace=True)
df_test_D12_f.reset_index(drop=True, inplace=True)

y_test_D12 = df_test_D12_f['Fault Type']
y_train_D12 = df_train_D12_f['Fault Type'] 
# preprocces it with normalizing  

df_train_D12n = pd.DataFrame(preprocessing.normalize(df_train_D12_f.drop(['Fault Type'], axis=1)), columns=df_train_D12_f.drop(['Fault Type'], axis=1).columns)
df_test_D12n = pd.DataFrame(preprocessing.normalize(df_test_D12_f.drop(['Fault Type'], axis=1)), columns=df_test_D12_f.drop(['Fault Type'], axis=1).columns)


In [91]:
import optuna
from sklearn import svm
from sklearn import metrics

# Define the objective function for Optuna
def objective(trial):
    # Define the search space for hyperparameters
    c = trial.suggest_float('C', 0.01, 10)
    gamma = trial.suggest_float('gamma', 0.01, 10)  # Adjusted to a common range for gamma
    kernel = trial.suggest_categorical('kernel', ['linear', 'poly', 'rbf', 'sigmoid'])
    degree = trial.suggest_int('degree', 1, 4) 
    shrinking = trial.suggest_categorical('shrinking', [True, False])
    tol = trial.suggest_float('tol', 1e-3, 1e-1)
    decision_function_shape = trial.suggest_categorical('decision_function_shape', ['ovo'])
    break_ties = trial.suggest_categorical('break_ties', [False])
    probability = trial.suggest_categorical('probability', [False,True])
    random_state = trial.suggest_int('random_state', 1, 100)
    # Create an SVM classifier with the hyperparameters
    clf = svm.SVC(C=c, gamma=gamma, kernel=kernel, degree=degree, shrinking=shrinking,tol=tol,
        decision_function_shape=decision_function_shape, break_ties=break_ties, probability=probability,random_state=random_state)

    # Fit the classifier on the training data
    clf.fit(df_train_D12n, y_train_D12)  # Assuming x_train_n and y_train_1 are defined

    # Predict the labels for the test data
    y_pred = clf.predict(df_test_D12n)  # Assuming x_test_n is defined

    # Calculate the accuracy of the classifier
    accuracy = metrics.accuracy_score(y_test_D12, y_pred)  # Assuming y_test_1 is defined

    # Return the accuracy
    return accuracy

# Create a study object and optimize the hyperparameters
study = optuna.create_study(direction='maximize')
study.optimize(objective, n_trials=2000)

# Get the best hyperparameters
best_params = study.best_params
best_accuracy = study.best_value

print('Best accuracy:', best_accuracy)
print('Best parameters:', best_params)

[I 2024-05-28 12:47:11,038] A new study created in memory with name: no-name-6c2d8f21-e7ef-4de1-b972-2a07921e3765
[I 2024-05-28 12:47:11,065] Trial 0 finished with value: 1.0 and parameters: {'C': 5.855026513187478, 'gamma': 0.4202649681879631, 'kernel': 'rbf', 'degree': 1, 'shrinking': True, 'tol': 0.0020874661890785766, 'decision_function_shape': 'ovo', 'break_ties': False, 'probability': True, 'random_state': 36}. Best is trial 0 with value: 1.0.
[I 2024-05-28 12:47:11,069] Trial 1 finished with value: 1.0 and parameters: {'C': 5.653677309348207, 'gamma': 8.006194393370029, 'kernel': 'rbf', 'degree': 3, 'shrinking': False, 'tol': 0.08427253777874527, 'decision_function_shape': 'ovo', 'break_ties': False, 'probability': True, 'random_state': 93}. Best is trial 0 with value: 1.0.
[I 2024-05-28 12:47:11,071] Trial 2 finished with value: 1.0 and parameters: {'C': 6.409057274380676, 'gamma': 8.85283725769805, 'kernel': 'linear', 'degree': 3, 'shrinking': True, 'tol': 0.05878944963451451,

Best accuracy: 1.0
Best parameters: {'C': 5.855026513187478, 'gamma': 0.4202649681879631, 'kernel': 'rbf', 'degree': 1, 'shrinking': True, 'tol': 0.0020874661890785766, 'decision_function_shape': 'ovo', 'break_ties': False, 'probability': True, 'random_state': 36}


# 3rd Layer (T1,T23 T2,T13 T3,T12)

## T1 T23

In [95]:
df_train_T_f23 = df_train_T_filtered.copy()
df_test_T_f23 = df_test_T_filtered.copy()

df_train_T_f23['Fault Type'] = df_train_T_f23['Fault Type'].replace([5, 6], 0)
df_test_T_f23['Fault Type'] = df_test_T_f23['Fault Type'].replace([5,6],0)  
df_train_T_f23['Fault Type'] = df_train_T_f23['Fault Type'].replace([4],1)  
df_test_T_f23['Fault Type'] = df_test_T_f23['Fault Type'].replace([4],1)  


df_train_T_f23.reset_index(drop=True, inplace=True)
df_test_T_f23.reset_index(drop=True, inplace=True)


y_test_T1_23 = df_test_T_f23['Fault Type']
y_train_T1_23 = df_train_T_f23['Fault Type']  

df_train_T1_23 = df_train_T_f23.drop('Fault Type',axis=1)
df_test_T1_23 = df_test_T_f23.drop('Fault Type',axis=1) 

df_train_T1_23n = pd.DataFrame(preprocessing.normalize(df_train_T1_23),columns=df_train_T1_23.columns)
df_test_T1_23n = pd.DataFrame(preprocessing.normalize(df_test_T1_23),columns=df_test_T1_23.columns) 

df_train_T_f23.head()

H2    CH4   C2H2  C2H4   C2H6  Fault Type
0   42.0  124.0  0.001   8.0    1.0           1
1   36.0   21.0  0.001   2.0   65.0           1
2  161.0   38.0  0.001  13.0  210.0           1
3   13.0   59.0  0.001  44.0  117.0           1
4   10.0   44.0  0.001  28.0  106.0           1

In [97]:
import optuna
from sklearn import svm
from sklearn import metrics

# Define the objective function for Optuna
def objective(trial):
    # Define the search space for hyperparameters
    c = trial.suggest_float('C', 0.01, 20)
    gamma = trial.suggest_float('gamma', 0.01, 20)  # Adjusted to a common range for gamma
    kernel = trial.suggest_categorical('kernel', ['linear', 'poly', 'rbf', 'sigmoid'])
    degree = trial.suggest_int('degree', 1, 4) 
    shrinking = trial.suggest_categorical('shrinking', [True, False])
    tol = trial.suggest_float('tol', 1e-3, 1e-1)
    decision_function_shape = trial.suggest_categorical('decision_function_shape', ['ovr'])
    break_ties = trial.suggest_categorical('break_ties', [True])
    probability = trial.suggest_categorical('probability', [False,True])
    random_state = trial.suggest_int('random_state', 1, 100)
    # Create an SVM classifier with the hyperparameters
    clf = svm.SVC(C=c, gamma=gamma, kernel=kernel, degree=degree, shrinking=shrinking,tol=tol,
        decision_function_shape=decision_function_shape, break_ties=break_ties, probability=probability ,random_state=random_state)

    # Fit the classifier on the training data
    clf.fit(df_train_T1_23n, y_train_T1_23)  # Assuming x_train_n and y_train_1 are defined

    # Predict the labels for the test data
    y_pred = clf.predict(df_test_T1_23n)  # Assuming x_test_n is defined

    # Calculate the accuracy of the classifier
    accuracy = metrics.accuracy_score(y_test_T1_23, y_pred)  # Assuming y_test_1 is defined

    # Return the accuracy
    return accuracy

# Create a study object and optimize the hyperparameters
study = optuna.create_study(direction='maximize')
study.optimize(objective, n_trials=1000)

# Get the best hyperparameters
best_params = study.best_params
best_accuracy = study.best_value

print('Best accuracy:', best_accuracy)
print('Best parameters:', best_params)


[I 2024-05-28 14:22:45,499] A new study created in memory with name: no-name-378f8caa-164c-4162-a569-749320f0addb
[I 2024-05-28 14:22:45,557] Trial 0 finished with value: 0.9868421052631579 and parameters: {'C': 13.980992941301498, 'gamma': 9.95525297743462, 'kernel': 'poly', 'degree': 2, 'shrinking': True, 'tol': 0.023712120546022356, 'decision_function_shape': 'ovr', 'break_ties': True, 'probability': True, 'random_state': 51}. Best is trial 0 with value: 0.9868421052631579.
[I 2024-05-28 14:22:45,569] Trial 1 finished with value: 1.0 and parameters: {'C': 9.635469498390801, 'gamma': 1.583182838402548, 'kernel': 'rbf', 'degree': 1, 'shrinking': True, 'tol': 0.03838761697844219, 'decision_function_shape': 'ovr', 'break_ties': True, 'probability': False, 'random_state': 30}. Best is trial 1 with value: 1.0.
[I 2024-05-28 14:22:45,586] Trial 2 finished with value: 0.9736842105263158 and parameters: {'C': 6.959016126892354, 'gamma': 8.251578661900298, 'kernel': 'linear', 'degree': 4, 'sh

Best accuracy: 1.0
Best parameters: {'C': 9.635469498390801, 'gamma': 1.583182838402548, 'kernel': 'rbf', 'degree': 1, 'shrinking': True, 'tol': 0.03838761697844219, 'decision_function_shape': 'ovr', 'break_ties': True, 'probability': False, 'random_state': 30}


## T23

In [96]:
df_test_T23 = df_test.copy()
df_train_T23 = df_train.copy() 

# Filter the training data
df_train_T23_f = df_train_T23[df_train_T23['Fault Type'].isin([5, 6])]
# Filter the test data
df_test_T23_f = df_test_T23[df_test_T23['Fault Type'].isin([5, 6])]

# Optionally, reset the index if needed
df_train_T23_f.reset_index(drop=True, inplace=True)
df_test_T23_f.reset_index(drop=True, inplace=True)

y_test_T23 = df_test_T23_f['Fault Type']
y_train_T23 = df_train_T23_f['Fault Type'] 
# preprocces it with normalizing  

df_train_T23n = pd.DataFrame(preprocessing.normalize(df_train_T23_f.drop(['Fault Type'], axis=1)), columns=df_train_T23_f.drop(['Fault Type'], axis=1).columns)
df_test_T23n = pd.DataFrame(preprocessing.normalize(df_test_T23_f.drop(['Fault Type'], axis=1)), columns=df_test_T23_f.drop(['Fault Type'], axis=1).columns)


In [99]:
import optuna
from sklearn import svm
from sklearn import metrics

# Define the objective function for Optuna
def objective(trial):
    # Define the search space for hyperparameters
    c = trial.suggest_float('C', 0.01, 5)
    gamma = trial.suggest_float('gamma', 0.01, 5)  # Adjusted to a common range for gamma
    kernel = trial.suggest_categorical('kernel', ['linear', 'poly', 'rbf', 'sigmoid'])
    degree = trial.suggest_int('degree', 1, 4) 
    shrinking = trial.suggest_categorical('shrinking', [True, False])
    tol = trial.suggest_float('tol', 1e-3, 1e-1)
    decision_function_shape = trial.suggest_categorical('decision_function_shape', ['ovo'])
    break_ties = trial.suggest_categorical('break_ties', [False])
    probability = trial.suggest_categorical('probability', [False,True])
    random_state = trial.suggest_int('random_state', 1, 100)
    # Create an SVM classifier with the hyperparameters
    clf = svm.SVC(C=c, gamma=gamma, kernel=kernel, degree=degree, shrinking=shrinking,tol=tol,
        decision_function_shape=decision_function_shape, break_ties=break_ties, probability=probability,random_state=random_state)

    # Fit the classifier on the training data
    clf.fit(df_train_T23n, y_train_T23)  # Assuming x_train_n and y_train_1 are defined

    # Predict the labels for the test data
    y_pred = clf.predict(df_test_T23n)  # Assuming x_test_n is defined

    # Calculate the accuracy of the classifier
    accuracy = metrics.accuracy_score(y_test_T23, y_pred)  # Assuming y_test_1 is defined

    # Return the accuracy
    return accuracy

# Create a study object and optimize the hyperparameters
study = optuna.create_study(direction='maximize')
study.optimize(objective, n_trials=2000)

# Get the best hyperparameters
best_params = study.best_params
best_accuracy = study.best_value

print('Best accuracy:', best_accuracy)
print('Best parameters:', best_params)

[I 2024-05-28 14:27:33,582] A new study created in memory with name: no-name-c18fcfc4-c781-4b0d-ab8e-bc9a84894e0e


[I 2024-05-28 14:27:33,618] Trial 0 finished with value: 0.6363636363636364 and parameters: {'C': 0.6832124828741626, 'gamma': 4.740301234174626, 'kernel': 'sigmoid', 'degree': 4, 'shrinking': True, 'tol': 0.006509279498482037, 'decision_function_shape': 'ovo', 'break_ties': False, 'probability': True, 'random_state': 32}. Best is trial 0 with value: 0.6363636363636364.
[I 2024-05-28 14:27:33,632] Trial 1 finished with value: 0.9545454545454546 and parameters: {'C': 3.3620508290448843, 'gamma': 4.335351646515828, 'kernel': 'poly', 'degree': 4, 'shrinking': True, 'tol': 0.05422848825501051, 'decision_function_shape': 'ovo', 'break_ties': False, 'probability': True, 'random_state': 2}. Best is trial 1 with value: 0.9545454545454546.
[I 2024-05-28 14:27:33,636] Trial 2 finished with value: 0.8409090909090909 and parameters: {'C': 4.299957108447156, 'gamma': 0.6638351530630029, 'kernel': 'sigmoid', 'degree': 2, 'shrinking': True, 'tol': 0.005873730113638771, 'decision_function_shape': 'ovo

Best accuracy: 0.9772727272727273
Best parameters: {'C': 4.64121174509, 'gamma': 4.502258897382112, 'kernel': 'poly', 'degree': 4, 'shrinking': True, 'tol': 0.07413643229045912, 'decision_function_shape': 'ovo', 'break_ties': False, 'probability': False, 'random_state': 30}


## T2 T13

In [101]:
df_train_T_f13 = df_train_T_filtered.copy()
df_test_T_f13 = df_test_T_filtered.copy()

df_train_T_f13['Fault Type'] = df_train_T_f13['Fault Type'].replace([4, 6], 0)
df_test_T_f13['Fault Type'] = df_test_T_f13['Fault Type'].replace([4,6],0)  
df_train_T_f13['Fault Type'] = df_train_T_f13['Fault Type'].replace([5],1)  
df_test_T_f13['Fault Type'] = df_test_T_f13['Fault Type'].replace([5],1)  


df_train_T_f13.reset_index(drop=True, inplace=True)
df_test_T_f13.reset_index(drop=True, inplace=True)


y_test_T1_13 = df_test_T_f13['Fault Type']
y_train_T1_13 = df_train_T_f13['Fault Type']  

df_train_T1_13 = df_train_T_f13.drop('Fault Type',axis=1)
df_test_T1_13 = df_test_T_f13.drop('Fault Type',axis=1) 

df_train_T1_13n = pd.DataFrame(preprocessing.normalize(df_train_T1_13),columns=df_train_T1_13.columns)
df_test_T1_13n = pd.DataFrame(preprocessing.normalize(df_test_T1_13),columns=df_test_T1_13.columns) 

df_train_T_f13.head()

H2    CH4   C2H2  C2H4   C2H6  Fault Type
0   42.0  124.0  0.001   8.0    1.0           0
1   36.0   21.0  0.001   2.0   65.0           0
2  161.0   38.0  0.001  13.0  210.0           0
3   13.0   59.0  0.001  44.0  117.0           0
4   10.0   44.0  0.001  28.0  106.0           0

In [102]:
import optuna
from sklearn import svm
from sklearn import metrics

# Define the objective function for Optuna
def objective(trial):
    # Define the search space for hyperparameters
    c = trial.suggest_float('C', 0.01, 20)
    gamma = trial.suggest_float('gamma', 0.01, 20)  # Adjusted to a common range for gamma
    kernel = trial.suggest_categorical('kernel', ['linear', 'poly', 'rbf', 'sigmoid'])
    degree = trial.suggest_int('degree', 1, 4) 
    shrinking = trial.suggest_categorical('shrinking', [True, False])
    tol = trial.suggest_float('tol', 1e-3, 1e-1)
    decision_function_shape = trial.suggest_categorical('decision_function_shape', ['ovr'])
    break_ties = trial.suggest_categorical('break_ties', [True])
    probability = trial.suggest_categorical('probability', [False,True])
    random_state = trial.suggest_int('random_state', 1, 100)
    # Create an SVM classifier with the hyperparameters
    clf = svm.SVC(C=c, gamma=gamma, kernel=kernel, degree=degree, shrinking=shrinking,tol=tol,
        decision_function_shape=decision_function_shape, break_ties=break_ties, probability=probability ,random_state=random_state)

    # Fit the classifier on the training data
    clf.fit(df_train_T1_13n, y_train_T1_13)  # Assuming x_train_n and y_train_1 are defined

    # Predict the labels for the test data
    y_pred = clf.predict(df_test_T1_13n)  # Assuming x_test_n is defined

    # Calculate the accuracy of the classifier
    accuracy = metrics.accuracy_score(y_test_T1_13, y_pred)  # Assuming y_test_1 is defined

    # Return the accuracy
    return accuracy

# Create a study object and optimize the hyperparameters
study = optuna.create_study(direction='maximize')
study.optimize(objective, n_trials=1000)

# Get the best hyperparameters
best_params = study.best_params
best_accuracy = study.best_value

print('Best accuracy:', best_accuracy)
print('Best parameters:', best_params)


[I 2024-05-28 14:35:26,235] A new study created in memory with name: no-name-6f9b838b-1a26-4548-ab55-335552a09470
[I 2024-05-28 14:35:26,275] Trial 0 finished with value: 0.9605263157894737 and parameters: {'C': 19.044385151381245, 'gamma': 2.7994543269434873, 'kernel': 'poly', 'degree': 2, 'shrinking': True, 'tol': 0.021418328168356548, 'decision_function_shape': 'ovr', 'break_ties': True, 'probability': True, 'random_state': 50}. Best is trial 0 with value: 0.9605263157894737.
[I 2024-05-28 14:35:26,279] Trial 1 finished with value: 0.9473684210526315 and parameters: {'C': 5.518777653496163, 'gamma': 14.422700681336948, 'kernel': 'rbf', 'degree': 3, 'shrinking': False, 'tol': 0.030852473092415053, 'decision_function_shape': 'ovr', 'break_ties': True, 'probability': False, 'random_state': 24}. Best is trial 0 with value: 0.9605263157894737.
[I 2024-05-28 14:35:26,284] Trial 2 finished with value: 0.7894736842105263 and parameters: {'C': 15.570550988848778, 'gamma': 14.518393236154031,

Best accuracy: 0.9736842105263158
Best parameters: {'C': 10.095603994672356, 'gamma': 15.772837268352774, 'kernel': 'poly', 'degree': 3, 'shrinking': True, 'tol': 0.03159647441915506, 'decision_function_shape': 'ovr', 'break_ties': True, 'probability': True, 'random_state': 29}


## T13

In [103]:
df_test_T13 = df_test.copy()
df_train_T13 = df_train.copy() 

# Filter the training data
df_train_T13_f = df_train_T13[df_train_T13['Fault Type'].isin([5, 6])]
# Filter the test data
df_test_T13_f = df_test_T13[df_test_T13['Fault Type'].isin([5, 6])]

# Optionally, reset the index if needed
df_train_T13_f.reset_index(drop=True, inplace=True)
df_test_T13_f.reset_index(drop=True, inplace=True)

y_test_T13 = df_test_T13_f['Fault Type']
y_train_T13 = df_train_T13_f['Fault Type'] 
# preprocces it with normalizing  

df_train_T13n = pd.DataFrame(preprocessing.normalize(df_train_T13_f.drop(['Fault Type'], axis=1)), columns=df_train_T13_f.drop(['Fault Type'], axis=1).columns)
df_test_T13n = pd.DataFrame(preprocessing.normalize(df_test_T13_f.drop(['Fault Type'], axis=1)), columns=df_test_T13_f.drop(['Fault Type'], axis=1).columns)


In [104]:
import optuna
from sklearn import svm
from sklearn import metrics

# Define the objective function for Optuna
def objective(trial):
    # Define the search space for hyperparameters
    c = trial.suggest_float('C', 0.01, 5)
    gamma = trial.suggest_float('gamma', 0.01, 5)  # Adjusted to a common range for gamma
    kernel = trial.suggest_categorical('kernel', ['linear', 'poly', 'rbf', 'sigmoid'])
    degree = trial.suggest_int('degree', 1, 4) 
    shrinking = trial.suggest_categorical('shrinking', [True, False])
    tol = trial.suggest_float('tol', 1e-3, 1e-1)
    decision_function_shape = trial.suggest_categorical('decision_function_shape', ['ovo'])
    break_ties = trial.suggest_categorical('break_ties', [False])
    probability = trial.suggest_categorical('probability', [False,True])
    random_state = trial.suggest_int('random_state', 1, 100)
    # Create an SVM classifier with the hyperparameters
    clf = svm.SVC(C=c, gamma=gamma, kernel=kernel, degree=degree, shrinking=shrinking,tol=tol,
        decision_function_shape=decision_function_shape, break_ties=break_ties, probability=probability,random_state=random_state)

    # Fit the classifier on the training data
    clf.fit(df_train_T13n, y_train_T13)  # Assuming x_train_n and y_train_1 are defined

    # Predict the labels for the test data
    y_pred = clf.predict(df_test_T13n)  # Assuming x_test_n is defined

    # Calculate the accuracy of the classifier
    accuracy = metrics.accuracy_score(y_test_T13, y_pred)  # Assuming y_test_1 is defined

    # Return the accuracy
    return accuracy

# Create a study object and optimize the hyperparameters
study = optuna.create_study(direction='maximize')
study.optimize(objective, n_trials=2000)

# Get the best hyperparameters
best_params = study.best_params
best_accuracy = study.best_value

print('Best accuracy:', best_accuracy)
print('Best parameters:', best_params)

[I 2024-05-28 15:20:09,661] A new study created in memory with name: no-name-25d56e46-6b87-4ba4-9132-3f6903d854be
[I 2024-05-28 15:20:09,717] Trial 0 finished with value: 0.6363636363636364 and parameters: {'C': 0.21223812220032207, 'gamma': 1.3421156846408209, 'kernel': 'sigmoid', 'degree': 2, 'shrinking': False, 'tol': 0.0447903559727549, 'decision_function_shape': 'ovo', 'break_ties': False, 'probability': False, 'random_state': 41}. Best is trial 0 with value: 0.6363636363636364.
[I 2024-05-28 15:20:09,727] Trial 1 finished with value: 0.6363636363636364 and parameters: {'C': 0.4245399103632137, 'gamma': 4.814186683880003, 'kernel': 'sigmoid', 'degree': 2, 'shrinking': True, 'tol': 0.0251386463773719, 'decision_function_shape': 'ovo', 'break_ties': False, 'probability': False, 'random_state': 74}. Best is trial 0 with value: 0.6363636363636364.
[I 2024-05-28 15:20:09,740] Trial 2 finished with value: 0.8636363636363636 and parameters: {'C': 2.1141165364075922, 'gamma': 3.0628725346

Best accuracy: 0.9772727272727273
Best parameters: {'C': 4.57422156171458, 'gamma': 4.619217052930448, 'kernel': 'poly', 'degree': 4, 'shrinking': False, 'tol': 0.09937819116820129, 'decision_function_shape': 'ovo', 'break_ties': False, 'probability': False, 'random_state': 28}


## T3 T12

In [109]:
df_train_T_f12 = df_train_T_filtered.copy()
df_test_T_f12 = df_test_T_filtered.copy()

df_train_T_f12['Fault Type'] = df_train_T_f12['Fault Type'].replace([4, 5], 0)
df_test_T_f12['Fault Type'] = df_test_T_f12['Fault Type'].replace([4,5],0)  
df_train_T_f12['Fault Type'] = df_train_T_f12['Fault Type'].replace([6],1)  
df_test_T_f12['Fault Type'] = df_test_T_f12['Fault Type'].replace([6],1)  


df_train_T_f12.reset_index(drop=True, inplace=True)
df_test_T_f12.reset_index(drop=True, inplace=True)


y_test_T3_12 = df_test_T_f12['Fault Type']
y_train_T3_12 = df_train_T_f12['Fault Type']  

df_train_T3_12 = df_train_T_f12.drop('Fault Type',axis=1)
df_test_T3_12 = df_test_T_f12.drop('Fault Type',axis=1) 

df_train_T3_12n = pd.DataFrame(preprocessing.normalize(df_train_T3_12),columns=df_train_T3_12.columns)
df_test_T3_12n = pd.DataFrame(preprocessing.normalize(df_test_T3_12),columns=df_test_T3_12.columns) 

df_train_T_f13.head()

H2    CH4   C2H2  C2H4   C2H6  Fault Type
0   42.0  124.0  0.001   8.0    1.0           0
1   36.0   21.0  0.001   2.0   65.0           0
2  161.0   38.0  0.001  13.0  210.0           0
3   13.0   59.0  0.001  44.0  117.0           0
4   10.0   44.0  0.001  28.0  106.0           0

In [110]:
import optuna
from sklearn import svm
from sklearn import metrics

# Define the objective function for Optuna
def objective(trial):
    # Define the search space for hyperparameters
    c = trial.suggest_float('C', 0.01, 20)
    gamma = trial.suggest_float('gamma', 0.01, 20)  # Adjusted to a common range for gamma
    kernel = trial.suggest_categorical('kernel', ['linear', 'poly', 'rbf', 'sigmoid'])
    degree = trial.suggest_int('degree', 1, 4) 
    shrinking = trial.suggest_categorical('shrinking', [True, False])
    tol = trial.suggest_float('tol', 1e-3, 1e-1)
    decision_function_shape = trial.suggest_categorical('decision_function_shape', ['ovr'])
    break_ties = trial.suggest_categorical('break_ties', [True])
    probability = trial.suggest_categorical('probability', [False,True])
    random_state = trial.suggest_int('random_state', 1, 100)
    # Create an SVM classifier with the hyperparameters
    clf = svm.SVC(C=c, gamma=gamma, kernel=kernel, degree=degree, shrinking=shrinking,tol=tol,
        decision_function_shape=decision_function_shape, break_ties=break_ties, probability=probability ,random_state=random_state)

    # Fit the classifier on the training data
    clf.fit(df_train_T3_12n, y_train_T3_12)  # Assuming x_train_n and y_train_1 are defined

    # Predict the labels for the test data
    y_pred = clf.predict(df_test_T3_12n)  # Assuming x_test_n is defined

    # Calculate the accuracy of the classifier
    accuracy = metrics.accuracy_score(y_test_T3_12, y_pred)  # Assuming y_test_1 is defined

    # Return the accuracy
    return accuracy

# Create a study object and optimize the hyperparameters
study = optuna.create_study(direction='maximize')
study.optimize(objective, n_trials=1000)

# Get the best hyperparameters
best_params = study.best_params
best_accuracy = study.best_value

print('Best accuracy:', best_accuracy)
print('Best parameters:', best_params)


[I 2024-05-28 15:30:56,651] A new study created in memory with name: no-name-8402aed8-5379-42cd-bd60-87115f166097
[I 2024-05-28 15:30:56,677] Trial 0 finished with value: 0.5921052631578947 and parameters: {'C': 5.3430538537491525, 'gamma': 8.432247746495971, 'kernel': 'sigmoid', 'degree': 1, 'shrinking': False, 'tol': 0.08674010982080822, 'decision_function_shape': 'ovr', 'break_ties': True, 'probability': True, 'random_state': 21}. Best is trial 0 with value: 0.5921052631578947.
[I 2024-05-28 15:30:56,683] Trial 1 finished with value: 0.9342105263157895 and parameters: {'C': 19.399461914214598, 'gamma': 5.804091596024982, 'kernel': 'linear', 'degree': 2, 'shrinking': False, 'tol': 0.08837404175607061, 'decision_function_shape': 'ovr', 'break_ties': True, 'probability': True, 'random_state': 96}. Best is trial 1 with value: 0.9342105263157895.
[I 2024-05-28 15:30:56,710] Trial 2 finished with value: 0.9210526315789473 and parameters: {'C': 17.445221641263878, 'gamma': 3.73592805609026

Best accuracy: 0.9736842105263158
Best parameters: {'C': 0.29075848338746646, 'gamma': 16.975153500236086, 'kernel': 'rbf', 'degree': 3, 'shrinking': False, 'tol': 0.06103733541986675, 'decision_function_shape': 'ovr', 'break_ties': True, 'probability': True, 'random_state': 66}


## T12

In [111]:
df_test_T12 = df_test.copy()
df_train_T12 = df_train.copy() 

# Filter the training data
df_train_T12_f = df_train_T12[df_train_T12['Fault Type'].isin([4, 5])]
# Filter the test data
df_test_T12_f = df_test_T12[df_test_T12['Fault Type'].isin([4, 5])]

# Optionally, reset the index if needed
df_train_T12_f.reset_index(drop=True, inplace=True)
df_test_T12_f.reset_index(drop=True, inplace=True)

y_test_T12 = df_test_T12_f['Fault Type']
y_train_T12 = df_train_T12_f['Fault Type'] 
# preprocces it with normalizing  

df_train_T12n = pd.DataFrame(preprocessing.normalize(df_train_T12_f.drop(['Fault Type'], axis=1)), columns=df_train_T12_f.drop(['Fault Type'], axis=1).columns)
df_test_T12n = pd.DataFrame(preprocessing.normalize(df_test_T12_f.drop(['Fault Type'], axis=1)), columns=df_test_T12_f.drop(['Fault Type'], axis=1).columns)


In [112]:
import optuna
from sklearn import svm
from sklearn import metrics

# Define the objective function for Optuna
def objective(trial):
    # Define the search space for hyperparameters
    c = trial.suggest_float('C', 0.01, 5)
    gamma = trial.suggest_float('gamma', 0.01, 5)  # Adjusted to a common range for gamma
    kernel = trial.suggest_categorical('kernel', ['linear', 'poly', 'rbf', 'sigmoid'])
    degree = trial.suggest_int('degree', 1, 4) 
    shrinking = trial.suggest_categorical('shrinking', [True, False])
    tol = trial.suggest_float('tol', 1e-3, 1e-1)
    decision_function_shape = trial.suggest_categorical('decision_function_shape', ['ovo'])
    break_ties = trial.suggest_categorical('break_ties', [False])
    probability = trial.suggest_categorical('probability', [False,True])
    random_state = trial.suggest_int('random_state', 1, 100)
    # Create an SVM classifier with the hyperparameters
    clf = svm.SVC(C=c, gamma=gamma, kernel=kernel, degree=degree, shrinking=shrinking,tol=tol,
        decision_function_shape=decision_function_shape, break_ties=break_ties, probability=probability,random_state=random_state)

    # Fit the classifier on the training data
    clf.fit(df_train_T12n, y_train_T12)  # Assuming x_train_n and y_train_1 are defined

    # Predict the labels for the test data
    y_pred = clf.predict(df_test_T12n)  # Assuming x_test_n is defined

    # Calculate the accuracy of the classifier
    accuracy = metrics.accuracy_score(y_test_T12, y_pred)  # Assuming y_test_1 is defined

    # Return the accuracy
    return accuracy

# Create a study object and optimize the hyperparameters
study = optuna.create_study(direction='maximize')
study.optimize(objective, n_trials=2000)

# Get the best hyperparameters
best_params = study.best_params
best_accuracy = study.best_value

print('Best accuracy:', best_accuracy)
print('Best parameters:', best_params)

[I 2024-05-28 15:32:39,907] A new study created in memory with name: no-name-6b68cd8d-f9c2-4261-9784-c619c5539605
[I 2024-05-28 15:32:39,922] Trial 0 finished with value: 0.9375 and parameters: {'C': 2.9141578980255405, 'gamma': 1.285465670446065, 'kernel': 'linear', 'degree': 2, 'shrinking': False, 'tol': 0.0010836157530217142, 'decision_function_shape': 'ovo', 'break_ties': False, 'probability': True, 'random_state': 70}. Best is trial 0 with value: 0.9375.
[I 2024-05-28 15:32:39,931] Trial 1 finished with value: 0.9375 and parameters: {'C': 3.0458360269189986, 'gamma': 3.2666783005972366, 'kernel': 'linear', 'degree': 4, 'shrinking': True, 'tol': 0.06565840531231623, 'decision_function_shape': 'ovo', 'break_ties': False, 'probability': True, 'random_state': 50}. Best is trial 0 with value: 0.9375.
[I 2024-05-28 15:32:39,936] Trial 2 finished with value: 0.625 and parameters: {'C': 3.8804699064979022, 'gamma': 4.035056055946731, 'kernel': 'sigmoid', 'degree': 2, 'shrinking': True, 't

Best accuracy: 1.0
Best parameters: {'C': 3.7718668495664174, 'gamma': 3.4982652765216113, 'kernel': 'rbf', 'degree': 3, 'shrinking': True, 'tol': 0.08929106871871753, 'decision_function_shape': 'ovo', 'break_ties': False, 'probability': False, 'random_state': 34}
